In [1]:
import numpy as np
import random

import torch
import torch.nn as nn
import torch.nn.functional as func
import torch.optim as optim

from matplotlib import pyplot as plt

from numpy import exp,arange
from pylab import meshgrid,cm,imshow,contour,clabel,colorbar,axis,title,show

In [2]:
# ==========
# helping methods
# ==========

# generate a list from lower and upper bound
def gen_list(p0, pn, delta, dig=5):
    ret = []
    i = p0
    while i < pn:
        ret.append(float(i))
        i += delta
        i = round(i, dig)
    return ret

# padding and zero padding
def padding(origin, a_list, b_list):
    return np.hstack((a_list, origin, b_list))

def zero_padding(origin, num):
    zero_list = [0 for i in range(num)]
    return padding(origin, zero_list, zero_list)

# trainning pairs
def gen_pair(u, x, t, length=3, num=1000):
    pairs = []
    for i in range(num):
        r = random.randint(0, t-2)
        current_t = u[r]
        next_t = u[r+1]
        p = random.randint(length, x-1-length)
        train = current_t[p-length:p+length+1]
        solu = next_t[p]
        pair = {'input': train, 'solu': solu}
        pairs.append(pair)
    return pairs

# trainning pairs (in average)
def gen_pair_ave(u, x, t, length=3, num=1000):
    pairs = []
    for i in range(num):
        r = random.randint(0, t-2)
        current_t = u[r]
        next_t = u[r+1]
        p = random.randint(length, x-2-length)
        train0 = current_t[p-length:p+length+2]
        solu1 = next_t[p]
        solu2 = next_t[p+1]
        train = []
        for j in range(len(train0)-1):
                train.append(0.5 * (train0[j] + train0[j+1]))
        solu = 0.5 * (solu1 + solu2)
        pair = {'input': train, 'solu': solu}
        pairs.append(pair)
    return pairs

In [3]:
# the analytical representation of exact solution
def heat_equ_analytical_solu(x, t):
    return np.sin(np.pi * x) * np.exp(-np.power(np.pi, 2) * t)

In [4]:
# restnet
class ResNet(nn.Module):
    def __init__(self, i, h, o):
        super(ResNet, self).__init__()
        self.linear1 = nn.Linear(i, h)
        self.relu1 = nn.ReLU()
        self.linear2 = nn.Linear(h, o)
        self.relu2 = nn.ReLU()
        
    def forward(self, x):
        out = self.linear1(x)
        out = self.relu1(out)
        out = self.linear2(out)
        out = self.relu2(out)
        return out + torch.mean(x)

    def load_model(self, save_path):
        self.load_state_dict(torch.load(save_path))

    def save_model(self, save_path):
        torch.save(self.state_dict(), save_path)

## $\Delta x=\frac{1}{20}$ $\Delta t=\frac{1}{20}$

In [5]:
x_1 = arange(0, 2 * np.pi, 1/20)
t_1 = arange(0, 2 * np.pi, 1/20)
X_1,T_1 = meshgrid(x_1, t_1) # grid of point
Z_1 = heat_equ_analytical_solu(X_1, T_1) # evaluation of the function on the grid

In [6]:
# preparing the trainning set
data_pairs_1 = gen_pair_ave(Z_1, len(Z_1[0]), len(Z_1), length=3, num=10000)
print(data_pairs_1)

[{'input': [3.0550588086757233e-11, 2.9027083672019358e-11, 2.6788836121908798e-11, 2.389095851942701e-11, 2.0404806228651473e-11, 1.6416219888857185e-11, 1.2023411733089035e-11], 'solu': 1.4585382997817253e-11}, {'input': [4.041730994097967e-09, 1.2025672151483064e-08, 1.9713501349580943e-08, 2.69159187190922e-08, 3.3455576840926597e-08, 3.9171447628243616e-08, 4.392278737237197e-08], 'solu': 1.6432115226220535e-08}, {'input': [1.1760737369694622e-25, 1.4618198876439683e-25, 1.7115711811826212e-25, 1.9191779118614771e-25, 2.0795281129639877e-25, 2.1886734303672e-25, 2.2439263441241074e-25], 'solu': 1.1716543253251628e-25}, {'input': [1.9228962769409513e-19, 2.08355715303851e-19, 2.19291393709852e-19, 2.2482739021630644e-19, 2.248273902163064e-19, 2.19291393709852e-19, 2.0835571530385096e-19], 'solu': 1.3725667775271825e-19}, {'input': [0.0006061529834867172, 0.0005912274853268579, 0.0005617440043067237, 0.0005184285215790941, 0.00046234760808456837, 0.00039488216203526204, 0.000317693

In [7]:
model_1 = ResNet(7, 6, 1)
optimizer_1 = optim.Adam(model_1.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_1 = nn.MSELoss()
model_1.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [8]:
list_of_loss_1 = []
list_of_output_1 = []
for data in data_pairs_1:
    output = model_1(torch.FloatTensor(data["input"]))
    loss = criterion_1(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_1.append(np.log10(loss.item()))
    list_of_output_1.append(output)
    model_1.zero_grad()
    loss.backward()
    optimizer_1.step()

<ipython-input-8-ac38450c9edb>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_1.append(np.log10(loss.item()))


In [9]:
list_of_loss_1_file = open('list_of_loss_11 xx.txt', 'w+')
for value in list_of_loss_1:
    list_of_loss_1_file.write(str(value)+" ")
list_of_loss_1_file.close()

list_of_output_1_file = open('list_of_output_11 xx.txt', 'w+')
for value in list_of_output_1:
    list_of_output_1_file.write(str(value)+" ")
list_of_output_1_file.close()

In [10]:
model_1.save_model("model_xx delta x=1 20 delta t=1 20")

## $\Delta x=\frac{1}{40}$ $\Delta t=\frac{1}{20}$

In [11]:
x_2 = arange(0, 2 * np.pi, 1/40)
t_2 = arange(0, 2 * np.pi, 1/20)
X_2,T_2 = meshgrid(x_2, t_2) # grid of point
Z_2 = heat_equ_analytical_solu(X_2, T_2) # evaluation of the function on the grid

In [12]:
# preparing the trainning set
data_pairs_2 = gen_pair_ave(Z_2, len(Z_2[0]), len(Z_2), length=3, num=10000)
print(data_pairs_2)

[{'input': [2.6951690809918773e-27, 2.9550971763722263e-27, 3.196806114990709e-27, 3.418805680864368e-27, 3.619727172847245e-27, 3.798331843128092e-27, 3.953518534522544e-27], 'solu': 2.0871741169351914e-27}, {'input': [-0.0015185005252301128, -0.001190875911083827, -0.0008559091509392918, -0.0005156654262605335, -0.00017224245275272422, 0.00017224245275272552, 0.0005156654262605348], 'solu': -0.000314812724429901}, {'input': [1.2582749791705802e-13, 1.1066465514634433e-13, 9.481952797692133e-14, 7.838980688682777e-14, 6.147678657002075e-14, 4.418474142090392e-14, 2.6620282648009722e-14], 'solu': 4.785682230537567e-14}, {'input': [1.3980806299925927e-22, 1.2546269952259725e-22, 1.1034381678279702e-22, 9.454462771948849e-23, 7.816253958701011e-23, 6.129855340629588e-23, 4.4056641259994556e-23], 'solu': 5.771930852223783e-23}, {'input': [-1.3024078211412225e-18, -1.1159271645563025e-18, -9.225664459184548e-19, -7.235177983570453e-19, -5.200084229746869e-19, -3.1329302274433694e-19, -1.04

In [13]:
model_2 = ResNet(7, 6, 1)
optimizer_2 = optim.Adam(model_2.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_2 = nn.MSELoss()
model_2.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [14]:
list_of_loss_2 = []
list_of_output_2 = []
for data in data_pairs_2:
    output = model_2(torch.FloatTensor(data["input"]))
    loss = criterion_2(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_2.append(np.log10(loss.item()))
    list_of_output_2.append(output)
    model_2.zero_grad()
    loss.backward()
    optimizer_2.step()

<ipython-input-14-de329c128c88>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_2.append(np.log10(loss.item()))


In [15]:
list_of_loss_2_file = open('list_of_loss_21 xx.txt', 'w+')
for value in list_of_loss_2:
    list_of_loss_2_file.write(str(value)+" ")
list_of_loss_2_file.close()

list_of_output_2_file = open('list_of_output_21 xx.txt', 'w+')
for value in list_of_output_2:
    list_of_output_2_file.write(str(value)+" ")
list_of_output_2_file.close()

In [16]:
model_2.save_model("model_xx delta x=1 40 delta t=1 20")

## $\Delta x=\frac{1}{80}$ $\Delta t=\frac{1}{20}$

In [17]:
x_3 = arange(0, 2 * np.pi, 1/80)
t_3 = arange(0, 2 * np.pi, 1/20)
X_3,T_3 = meshgrid(x_3, t_3) # grid of point
Z_3 = heat_equ_analytical_solu(X_3, T_3) # evaluation of the function on the grid

In [18]:
# preparing the trainning set
data_pairs_3 = gen_pair_ave(Z_3, len(Z_3[0]), len(Z_3), length=3, num=10000)
print(data_pairs_3)

[{'input': [-2.6022938605289665e-20, -2.774598812461939e-20, -2.9426255341330214e-20, -3.106114940516232e-20, -3.2648149427968686e-20, -3.4184808370742196e-20, -3.566875681677236e-20], 'solu': -1.8962770374337538e-20}, {'input': [-4.558026706463515e-11, -4.2749693617263245e-11, -3.985320324089325e-11, -3.6895262113743585e-11, -3.388043116663648e-11, -3.081335905037318e-11, -2.7698774967850898e-11], 'solu': -2.252448466210434e-11}, {'input': [0.00022468910971236943, 0.00021286266739741074, 0.00020070800627791917, 0.00018824386796035324, 0.00017548947124258017, 0.00016246448247988135, 0.00014918898526085974], 'solu': 0.00011492250965819101}, {'input': [1.761581688926841e-19, 1.9882114705963827e-19, 2.211775574286707e-19, 2.4319292803541775e-19, 2.6483331277410917e-19, 2.860653437400044e-19, 3.068562826802818e-19], 'solu': 1.4846880232423005e-19}, {'input': [6.186530710085969e-13, 1.855005294831155e-12, 3.088497234942549e-12, 4.317226936176407e-12, 5.539299786393476e-12, 6.752831437836439

In [19]:
model_3 = ResNet(7, 6, 1)
optimizer_3 = optim.Adam(model_3.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_3 = nn.MSELoss()
model_3.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [20]:
list_of_loss_3 = []
list_of_output_3 = []
for data in data_pairs_3:
    output = model_3(torch.FloatTensor(data["input"]))
    loss = criterion_3(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_3.append(np.log10(loss.item()))
    list_of_output_3.append(output)
    model_3.zero_grad()
    loss.backward()
    optimizer_3.step()

<ipython-input-20-3f959fb14d49>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_3.append(np.log10(loss.item()))


In [21]:
list_of_loss_3_file = open('list_of_loss_31 xx.txt', 'w+')
for value in list_of_loss_3:
    list_of_loss_3_file.write(str(value)+" ")
list_of_loss_3_file.close()

list_of_output_3_file = open('list_of_output_31 xx.txt', 'w+')
for value in list_of_output_3:
    list_of_output_3_file.write(str(value)+" ")
list_of_output_3_file.close()

In [22]:
model_3.save_model("model_xx delta x=1 80 delta t=1 20")

## $\Delta x=\frac{1}{160}$ $\Delta t=\frac{1}{20}$

In [23]:
x_4 = arange(0, 2 * np.pi, 1/160)
t_4 = arange(0, 2 * np.pi, 1/20)
X_4,T_4 = meshgrid(x_4, t_4) # grid of point
Z_4 = heat_equ_analytical_solu(X_4, T_4) # evaluation of the function on the grid

In [24]:
# preparing the trainning set
data_pairs_4 = gen_pair_ave(Z_4, len(Z_4[0]), len(Z_4), length=3, num=10000)
print(data_pairs_4)

[{'input': [4.8734034643582627e-23, 2.924793797399362e-23, 9.750565667556564e-24, -9.750565667556717e-24, -2.924793797399465e-23, -4.873403464358366e-23, -6.82013434151228e-23], 'solu': -5.95270108526787e-24}, {'input': [0.00047321017335285806, 0.0005588169352485552, 0.0006442082625781455, 0.0007293512353594451, 0.000814213029355678, 0.0008987609287298426, 0.0009829623386572854], 'solu': 0.0004452674889121105}, {'input': [0.19282172254276453, 0.1904131763615884, 0.18793122227624431, 0.18537681712727838, 0.18275094568650085, 0.18005462027733785, 0.1772888803845616], 'solu': 0.11317218078626227}, {'input': [-4.303312094819806e-15, -4.670278547607239e-15, -5.035444519111754e-15, -5.398669230900083e-15, -5.7598126529315155e-15, -6.118735557542213e-15, -6.475299573120022e-15], 'solu': -3.2958769045277287e-15}, {'input': [5.629870849621116e-19, 5.673304543296446e-19, 5.714551070074043e-19, 5.753594528632677e-19, 5.790419866975844e-19, 5.825012888234609e-19, 5.857360256140772e-19], 'solu': 3.

In [25]:
model_4 = ResNet(7, 6, 1)
optimizer_4 = optim.Adam(model_4.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_4 = nn.MSELoss()
model_4.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [ ]:
list_of_loss_4 = []
list_of_output_4 = []
for data in data_pairs_4:
    output = model_4(torch.FloatTensor(data["input"]))
    loss = criterion_4(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_4.append(np.log10(loss.item()))
    list_of_output_4.append(output)
    model_4.zero_grad()
    loss.backward()
    optimizer_4.step()

<ipython-input-26-f52da78e2a74>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_4.append(np.log10(loss.item()))


In [ ]:
list_of_loss_4_file = open('list_of_loss_41 xx.txt', 'w+')
for value in list_of_loss_4:
    list_of_loss_4_file.write(str(value)+" ")
list_of_loss_4_file.close()

list_of_output_4_file = open('list_of_output_41 xx.txt', 'w+')
for value in list_of_output_4:
    list_of_output_4_file.write(str(value)+" ")
list_of_output_4_file.close()

In [ ]:
model_4.save_model("model_xx delta x=1 160 delta t=1 20")